# V0 - V3

In [ ]:
%pip install openreview-py numpy pandas nltk transformers tqdm torch
%pip install torch torchvision torchaudio
%pip install pylats taaled spacy convokit textstat simpletransformers

# English models
# %python -m spacy download en_core_web_sm
# %python -m spacy download en_core_web_trf
# # Spanish models (used as fallback)
# %python -m spacy download es_core_news_sm
# %python -m spacy download es_dep_news_trf

In [1]:
import torch
print("Is GPU available? ", torch.cuda.is_available())

Is GPU available?  True


In [1]:
import json
import csv
from datetime import datetime
import pickle
import sys
import io
import re
import nltk
from nltk.tokenize import sent_tokenize
nltk.download('punkt')
nltk.download('punkt_tab')
import csv
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from tqdm import tqdm
from taaled import ld
from pylats import lats
import pandas as pd
import json
import pickle
import numpy as np


# ICLR 2024
# file_path = '/home/ali/Review_Quality_Benchmark/data/raw/OpenReview/ICLR2024/ICLR2024_submissions.pkl'

# NEURIPS 2023
file_path = '/home/ali/Review_Quality_Benchmark/data/raw/OpenReview/neurips2023/neurips2023_submissions.pkl'

with open(file_path, 'rb') as pkl_file:
    data = pickle.load(pkl_file)

[nltk_data] Downloading package punkt to /home/ali/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /home/ali/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
/home/ali/Review_Quality_Benchmark/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


plotnine has not been installed.
To enable advanced data visualization features, please install plotnine.
Attempting to load spacy model: en_core_web_sm
Successfully loaded spacy model: en_core_web_sm
Attempting to load spacy model: en_core_web_trf
Successfully loaded spacy model: en_core_web_trf
Attempting to load spacy model: es_core_news_sm
Successfully loaded spacy model: es_core_news_sm
Attempting to load spacy model: es_dep_news_trf
Successfully loaded spacy model: es_dep_news_trf


In [4]:
import pandas as pd
import json
import pickle
import numpy as np


# Replace 'your_file.pkl' with the path to your .pkl file
file_path = '/home/ali/Review_Quality_Benchmark/data/raw/OpenReview/neurips2023/neurips2023_submissions.pkl'
output_json_path = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v0.json'

# Load the .pkl file
with open(file_path, 'rb') as pkl_file:
    data = pickle.load(pkl_file)

# Extract the required fields for each submission
extracted_data = []
for submission in data:
    extracted_data.append({
        'number': submission.number if hasattr(submission, 'number') else np.nan,
        'id': submission.id if hasattr(submission, 'id') else np.nan,
        'content.paperhash': submission.content['paperhash']['value'] if 'paperhash' in submission.content and 'value' in submission.content['paperhash'] else np.nan,
        'content.authorids': submission.content['authorids']['value'] if 'authorids' in submission.content and 'value' in submission.content['authorids'] else np.nan,
        'cdate': submission.cdate if hasattr(submission, 'cdate') else np.nan,
        'content.title': submission.content['title']['value'] if 'title' in submission.content and 'value' in submission.content['title'] else np.nan,
        'content.abstract': submission.content['abstract']['value'] if 'abstract' in submission.content and 'value' in submission.content['abstract'] else np.nan,
        # 'content.TLDR': submission.content['TLDR']['value'] if 'TLDR' in submission.content and 'value' in submission.content['TLDR'] else np.nan,
    })

# Create a Pandas DataFrame
df = pd.DataFrame(extracted_data)

# Save the DataFrame to a JSON file
df.to_json(output_json_path, orient='records', indent=4)

print(f"DataFrame saved to JSON file at: {output_json_path}")

DataFrame saved to JSON file at: /home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v0.json


In [5]:
# Load the JSON file as a pandas DataFrame
df_json = pd.read_json('/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v0.json')

# Display the header of the first 5 samples
df_json

number          id                                  content.paperhash  \
0      10819  zyhxRc9bew  sun|what_is_flagged_in_uncertainty_quantificat...   
1      15594  zyZkaqNnpa  puli|dont_blame_dataset_shift_shortcut_learnin...   
2        327  zuXyQsXVLF  xu|enhancing_adversarial_contrastive_learning_...   
3        801  ztqf6bzuqQ  shi|hybrid_distillation_connecting_masked_auto...   
4       7411  ztDxO15N7f  scholkemper|an_optimizationbased_approach_to_n...   
...      ...         ...                                                ...   
3390   12557  05P1U0jk8r  sakos|exploiting_hidden_structures_in_nonconve...   
3391   12654  02Uc0G2Cym  mianjy|robustness_guarantees_for_adversarially...   
3392    1581  01GQK1gwe3  holl|can_neural_networks_improve_classical_opt...   
3393    6838  00EKYYu3fD  hu|complexity_matters_rethinking_the_latent_sp...   
3394   10107  009LK0vLcY  ghadiri|finite_population_regression_adjustmen...   

                                      content.authorids          cdate  \
0     [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...  1683789038840   
1     [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...  1683835167534   
2     [~Xilie_Xu1, ~Jingfeng_Zhang1, ~Feng_Liu2, ~Ma...  1682066194522   
3     [~Bowen_Shi2, ~XIAOPENG_ZHANG7, ~Yaoming_Wang1...  1682507396411   
4           [~Michael_Scholkemper1, ~Michael_T_Schaub1]  1683729208530   
...                                                 ...            ...   
3390  [~Iosif_Sakos1, ~Emmanouil-Vasileios_Vlatakis-...  1683812282551   
3391                   [~Poorya_Mianjy1, ~Raman_Arora1]  1683813240757   
3392                   [~Philipp_Holl1, ~Nils_Thuerey1]  1683105912880   
3393  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...  1683719044332   
3394  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...  1683778565991   

                                          content.title  \
0     What is Flagged in Uncertainty Quantification?...   
1     Don’t blame Dataset Shift! Shortcut Learning d...   
2     Enhancing Adversarial Contrastive Learning via...   
3     Hybrid Distillation: Connecting Masked Autoenc...   
4     An Optimization-based Approach To Node Role Di...   
...                                                 ...   
3390  Exploiting hidden structures in non-convex gam...   
3391  Robustness Guarantees for Adversarially Traine...   
3392  Can Neural Networks Improve Classical Optimiza...   
3393  Complexity Matters: Rethinking the Latent Spac...   
3394  Finite Population Regression Adjustment and No...   

                                       content.abstract  
0     Uncertainty quantification (UQ) is essential f...  
1     Common explanations for shortcut learning assu...  
2     Adversarial contrastive learning (ACL) is a te...  
3     Representation learning has been evolving from...  
4     Similar to community detection, partitioning t...  
...                                                 ...  
3390  A wide array of modern machine learning applic...  
3391  We study robust adversarial training of two-la...  
3392  Finding the values of model parameters from da...  
3393  In generative modeling, numerous successful ap...  
3394  The design and analysis of randomized experime...  

[3395 rows x 7 columns]

In [6]:
# Print the dimensions of the dataframe
print(f"Dimensions of the dataframe: {df.shape}")

# Count the number of NaN values in each column
print("Number of NaN values in each column:")
print(df.isna().sum())

Dimensions of the dataframe: (3395, 7)
Number of NaN values in each column:
number               0
id                   0
content.paperhash    0
content.authorids    0
cdate                0
content.title        0
content.abstract     0
dtype: int64


In [8]:
# number of review, comments, and meta-reviews for each submission
# 3395 is the number of submissions
num_of_reviews = [len(data[i].details['directReplies']) for i in range(3395)]
print('min:', min(num_of_reviews))
print('max:', max(num_of_reviews))
print('mean:', np.mean(num_of_reviews))
print('median:', np.median(num_of_reviews))
print('std:', np.std(num_of_reviews))
print('percentiles:', np.percentile(num_of_reviews, [25, 50, 75, 90, 95, 99]))

min: 4
max: 14
mean: 6.455670103092784
median: 6.0
std: 0.905242195033333
percentiles: [6. 6. 7. 8. 8. 9.]


In [10]:
comment_types = set()
for i in range(3395):
    for j in range(len(data[i].details['directReplies'])):
        comment_types.add(data[i].details['directReplies'][j]['invitations'][0].split('/')[-1])

comment_types

{'Author_Rebuttal', 'Decision', 'Official_Comment', 'Official_Review'}

In [11]:
# Iterate through each submission in the data
new_rows = []
for submission in data:
    submission_id = submission.id
    submission_number = submission.number
    submission_title = submission.content['title']['value'] if 'title' in submission.content and 'value' in submission.content['title'] else None
    submission_abstract = submission.content['abstract']['value'] if 'abstract' in submission.content and 'value' in submission.content['abstract'] else None
    submission_authors = submission.content['authorids']['value'] if 'authorids' in submission.content and 'value' in submission.content['authorids'] else np.nan
    submission_creation_date = submission.cdate if hasattr(submission, 'cdate') else np.nan

    # Check if 'directReplies' exists in details
    if 'directReplies' in submission.details:
        for reply in submission.details['directReplies']:
            # Check if the invitation is 'Official_Review'
            if reply['invitations'][0].split('/')[-1] == 'Official_Review':
                # Extract features from the review
                reviewer = reply['signatures'][0].split('/')[-1]  # if 'signatures' in reply and len(reply['signatures']) > 0 else None
                
                #'tcdate', 'cdate', 'tmdate', 'mdate'
                review_tcdate = reply['tcdate'] if 'tcdate' in reply else None
                review_cdate = reply['cdate'] if 'cdate' in reply else None
                review_tmdate = reply['tmdate'] if 'tmdate' in reply else None
                review_mdate = reply['mdate'] if 'mdate' in reply else None
                
                review_rating = int(reply['content']['rating']['value'].split(':')[0]) if 'rating' in reply['content'] and 'value' in reply['content']['rating'] else None
                review_confidence = int(reply['content']['confidence']['value'].split(':')[0]) if 'confidence' in reply['content'] and 'value' in reply['content']['confidence'] else None
                review_soundness = int(reply['content']['soundness']['value'].split(' ')[0]) if 'soundness' in reply['content'] and 'value' in reply['content']['soundness'] else None
                review_presentation = int(reply['content']['presentation']['value'].split(' ')[0]) if 'presentation' in reply['content'] and 'value' in reply['content']['presentation'] else None
                review_contribution = int(reply['content']['contribution']['value'].split(' ')[0]) if 'contribution' in reply['content'] and 'value' in reply['content']['contribution'] else None
                
                review_summary = reply['content']['summary']['value'] if 'summary' in reply['content'] and 'value' in reply['content']['summary'] else None
                review_strengths = reply['content']['strengths']['value'] if 'strengths' in reply['content'] and 'value' in reply['content']['strengths'] else None
                review_weaknesses = reply['content']['weaknesses']['value'] if 'weaknesses' in reply['content'] and 'value' in reply['content']['weaknesses'] else None
                review_questions = reply['content']['questions']['value'] if 'questions' in reply['content'] and 'value' in reply['content']['questions'] else None
                review_limitations = reply['content']['limitations']['value'] if 'limitations' in reply['content'] and 'value' in reply['content']['limitations'] else None
                
                # Create a new row with the extracted features
                new_row = {
                    'submission_id': submission_id,
                    'submission_number': submission_number,
                    'submission_creation_date': submission_creation_date,
                    'submission_authors': submission_authors,
                    
                    'submission_title': submission_title,
                    'submission_abstract': submission_abstract,
                    
                    'reviewer': reviewer,
                    'review_tcdate': review_tcdate,
                    'review_cdate': review_cdate,
                    'review_tmdate': review_tmdate,
                    'review_mdate': review_mdate,
                    
                    'review_summary': review_summary,
                    'review_strengths': review_strengths,
                    'review_weaknesses': review_weaknesses,
                    'review_questions': review_questions,
                    'review_limitations': review_limitations,
                    
                    'review_rating': review_rating,
                    'review_confidence': review_confidence,
                    'review_soundness': review_soundness,
                    'review_presentation': review_presentation,
                    'review_contribution': review_contribution
                }
                new_rows.append(new_row)

# Create a new DataFrame from the new rows
df_reviews = pd.DataFrame(new_rows)

# Save the updated DataFrame to a JSON file
output_json_path = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v1.json'
df_reviews.to_json(output_json_path, orient='records', indent=4)

print(f"Updated DataFrame with reviews saved to JSON file at: {output_json_path}")

Updated DataFrame with reviews saved to JSON file at: /home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v1.json


In [12]:
# Load the JSON file as a pandas DataFrame
df_reviews = pd.read_json('/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v1.json')

# Display the header of the first 5 samples
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       review_tcdate   review_cdate  review_tmdate  ...  \
0      1688368213177  1688368213177  1702411303415  ...   
1      1688505633161  1688505633161  1702411303319  ...   
2      1688552936677  1688552936677  1702411303221  ...   
3      1688657604892  1688657604892  1702411303144  ...   
4      1688617232745  1688617232745  1702411520565  ...   
...              ...            ...            ...  ...   
15170  1688676041356  1688676041356  1702411081106  ...   
15171  1688449656890  1688449656890  1702411268900  ...   
15172  1688485585833  1688485585833  1702411268818  ...   
15173  1688665406904  1688665406904  1702411268706  ...   
15174  1688755793651  1688755793651  1702411268608  ...   

                                          review_summary  \
0      This paper proposes a model-agnostic framework...   
1      In this pa

In [13]:
# Concatenate the specified columns into a single column named 'total_review'
df_reviews['total_review'] = df_reviews[['review_summary', 'review_strengths', 'review_weaknesses', 'review_questions', 'review_limitations']].apply(
    lambda row: ' '.join(row.dropna()), axis=1
)

# Drop the original columns to reduce redundancy
df_reviews = df_reviews.drop(columns=['review_summary', 'review_strengths', 'review_weaknesses', 'review_questions', 'review_limitations'])
# Create a new column 'length_words' to count the number of words in the 'total_review' column
df_reviews['length_words'] = df_reviews['total_review'].apply(lambda x: len(x.split()))


# Save the new DataFrame to a different JSON file
new_output_json_path = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_ICLR2024_total_review.json'
df_reviews.to_json(new_output_json_path, orient='records', indent=4)

print(f"New DataFrame with 'total_review' column saved to JSON file at: {new_output_json_path}")

New DataFrame with 'total_review' column saved to JSON file at: /home/ali/Review_Quality_Benchmark/data/processed/openreview_ICLR2024_total_review.json


In [15]:
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       review_tcdate   review_cdate  review_tmdate   review_mdate  \
0      1688368213177  1688368213177  1702411303415  1702411303415   
1      1688505633161  1688505633161  1702411303319  1702411303319   
2      1688552936677  1688552936677  1702411303221  1702411303221   
3      1688657604892  1688657604892  1702411303144  1702411303144   
4      1688617232745  1688617232745  1702411520565  1702411520565   
...              ...            ...            ...            ...   
15170  1688676041356  1688676041356  1702411081106  1702411081106   
15171  1688449656890  1688449656890  1702411268900  1702411268900   
15172  1688485585833  1688485585833  1702411268818  1702411268818   
15173  1688665406904  1688665406904  1702411268706  1702411268706   
15174  1688755793651  1688755793651  1702411268608  1702411268608   

       review_rat

In [16]:
import re


def count_citations(text):
    citation_patterns = [
        r'\[\d+(?:,\s*\d+)*\]',                         # [1], [1, 2, 3]
        r'\([A-Za-z]+ et al\.,\s*\d{4}\)',               # (Smith et al., 2020)
        r'\(\d{4}[a-z]?\)',                              # (2020), (2020a)
        r'\[[A-Za-z]+\d{4}[a-z]?\]',                     # [Smith2020], [Johnson2021a]
        r'\b(?:doi:|arxiv:|https?://[^\s]+)',             # DOI, arXiv, URLs
    ]
    pattern = '|'.join(citation_patterns)
    matches = re.findall(pattern, text)
    return len(matches)


# Apply the count_citations function to the 'total_review' column and create a new column 'citation_count'
df_reviews['citation_count'] = df_reviews['total_review'].apply(count_citations)
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       review_tcdate   review_cdate  review_tmdate   review_mdate  \
0      1688368213177  1688368213177  1702411303415  1702411303415   
1      1688505633161  1688505633161  1702411303319  1702411303319   
2      1688552936677  1688552936677  1702411303221  1702411303221   
3      1688657604892  1688657604892  1702411303144  1702411303144   
4      1688617232745  1688617232745  1702411520565  1702411520565   
...              ...            ...            ...            ...   
15170  1688676041356  1688676041356  1702411081106  1702411081106   
15171  1688449656890  1688449656890  1702411268900  1702411268900   
15172  1688485585833  1688485585833  1702411268818  1702411268818   
15173  1688665406904  1688665406904  1702411268706  1702411268706   
15174  1688755793651  1688755793651  1702411268608  1702411268608   

       review_rat

In [18]:
import csv
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from tqdm import tqdm


device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
tokenizer = AutoTokenizer.from_pretrained("shahrukhx01/bert-mini-finetune-question-detection")
model = AutoModelForSequenceClassification.from_pretrained("shahrukhx01/bert-mini-finetune-question-detection")
model.to(device)
model.eval()


def count_questions(review_text):
    
    if review_text:
        question_count = 0

        sentences = sent_tokenize(review_text)
        for sent in sentences:
            inputs = tokenizer(
                sent,
                return_tensors="pt",
                truncation=True,
                max_length=64,
                padding=True
            ).to(device)
            with torch.no_grad():
                outputs = model(**inputs)
                predicted = torch.argmax(outputs.logits, dim=1).item()

                # Label 0 = question
                if predicted == 0:
                    question_count += 1

    return question_count


df_reviews['question_count'] = [
    count_questions(row['total_review']) for row in tqdm(df_reviews.to_dict('records'), desc="Processing reviews")
]
df_reviews

2025-05-08 14:15:26.522604: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1746728126.544830 3911350 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1746728126.551650 3911350 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1746728126.571549 3911350 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1746728126.571568 3911350 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1746728126.571570 3911350 computation_placer.cc:177] computation placer alr

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       review_tcdate   review_cdate  review_tmdate   review_mdate  \
0      1688368213177  1688368213177  1702411303415  1702411303415   
1      1688505633161  1688505633161  1702411303319  1702411303319   
2      1688552936677  1688552936677  1702411303221  1702411303221   
3      1688657604892  1688657604892  1702411303144  1702411303144   
4      1688617232745  1688617232745  1702411520565  1702411520565   
...              ...            ...            ...            ...   
15170  1688676041356  1688676041356  1702411081106  1702411081106   
15171  1688449656890  1688449656890  1702411268900  1702411268900   
15172  1688485585833  1688485585833  1702411268818  1702411268818   
15173  1688665406904  1688665406904  1702411268706  1702411268706   
15174  1688755793651  1688755793651  1702411268608  1702411268608   

       review_rat

In [19]:
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       review_tcdate   review_cdate  review_tmdate   review_mdate  \
0      1688368213177  1688368213177  1702411303415  1702411303415   
1      1688505633161  1688505633161  1702411303319  1702411303319   
2      1688552936677  1688552936677  1702411303221  1702411303221   
3      1688657604892  1688657604892  1702411303144  1702411303144   
4      1688617232745  1688617232745  1702411520565  1702411520565   
...              ...            ...            ...            ...   
15170  1688676041356  1688676041356  1702411081106  1702411081106   
15171  1688449656890  1688449656890  1702411268900  1702411268900   
15172  1688485585833  1688485585833  1702411268818  1702411268818   
15173  1688665406904  1688665406904  1702411268706  1702411268706   
15174  1688755793651  1688755793651  1702411268608  1702411268608   

       review_rat

In [20]:
# Count rows where cdate and tcdate are equal or not equal
cdate_tcdate_equal = (df_reviews['review_cdate'] == df_reviews['review_tcdate']).sum()
cdate_tcdate_not_equal = (df_reviews['review_cdate'] != df_reviews['review_tcdate']).sum()

# Count rows where tmdate and mdate are equal or not equal
tmdate_mdate_equal = (df_reviews['review_tmdate'] == df_reviews['review_mdate']).sum()
tmdate_mdate_not_equal = (df_reviews['review_tmdate'] != df_reviews['review_mdate']).sum()

# Print the results
print(f"cdate and tcdate equal: {cdate_tcdate_equal}")
print(f"cdate and tcdate not equal: {cdate_tcdate_not_equal}")
print(f"tmdate and mdate equal: {tmdate_mdate_equal}")
print(f"tmdate and mdate not equal: {tmdate_mdate_not_equal}")

cdate and tcdate equal: 15175
cdate and tcdate not equal: 0
tmdate and mdate equal: 15175
tmdate and mdate not equal: 0


In [21]:
# Drop the 'tcdate' and 'tmdate' columns
df_reviews = df_reviews.drop(columns=['review_tcdate', 'review_tmdate'])

# Rename 'cdate' to 'creation_date' and 'mdate' to 'last_modification_date'
df_reviews = df_reviews.rename(columns={'review_cdate': 'creation_date', 'review_mdate': 'last_modification_date'})

# Display the updated DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  \
0      1688368213177           1702411303415              6   
1      1688505633161           1702411303319              6   
2      1688552936677           1702411303221              6   
3      1688657604892           1702411303144              6   
4      1688617232745           1702411520565              6   
...              ...                     ...            ...   
15170  1688676041356           1702411081106              6   
15171  1688449656890           1702411268900              7   
15172  1688485585833           1702411268818              5   
15173  1688665406904           1702411268706              4   
15174  1688755793651           1702411268608              4   

       review_confidence  review_soundness  review_presentation  \
0                     

In [23]:
# Save the new DataFrame to a different JSON file
out = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v2.json'
df_reviews.to_json(out, orient='records', indent=4)

# V4

In [ ]:
%pip install spacy

# English models
!python -m spacy download en_core_web_sm
!python -m spacy download en_core_web_trf
# # Spanish models (used as fallback)
!python -m spacy download es_core_news_sm
!python -m spacy download es_dep_news_trf

In [3]:
# Read the JSON file as a pandas DataFrame
df_reviews = pd.read_json('/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v2.json')

# Display the first few rows of the DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  \
0      1688368213177           1702411303415              6   
1      1688505633161           1702411303319              6   
2      1688552936677           1702411303221              6   
3      1688657604892           1702411303144              6   
4      1688617232745           1702411520565              6   
...              ...                     ...            ...   
15170  1688676041356           1702411081106              6   
15171  1688449656890           1702411268900              7   
15172  1688485585833           1702411268818              5   
15173  1688665406904           1702411268706              4   
15174  1688755793651           1702411268608              4   

       review_confidence  review_soundness  review_presentation  \
0                     

In [4]:
from taaled import ld
from pylats import lats


def compute_mattr(review_text):
    mattr_value = ""
    if review_text is not None:
        review_text = review_text.strip()  # Remove leading/trailing whitespace
        review_text = review_text.replace('\n', '')  # Replace newlines with spaces
        try:
            cleaned = lats.Normalize(review_text, lats.ld_params_en)
            tokens = cleaned.toks
            mattr_value = f"{ld.lexdiv(tokens).mattr:.4f}"
        except Exception as e:
            mattr_value = ""
    return mattr_value


df_reviews['mattr'] = [
    compute_mattr(row['total_review']) for row in tqdm(df_reviews.to_dict('records'), desc="Processing reviews")
]
df_reviews

Processing reviews: 100%|██████████| 15175/15175 [40:43<00:00,  6.21it/s]  


submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  \
0      1688368213177           1702411303415              6   
1      1688505633161           1702411303319              6   
2      1688552936677           1702411303221              6   
3      1688657604892           1702411303144              6   
4      1688617232745           1702411520565              6   
...              ...                     ...            ...   
15170  1688676041356           1702411081106              6   
15171  1688449656890           1702411268900              7   
15172  1688485585833           1702411268818              5   
15173  1688665406904           1702411268706              4   
15174  1688755793651           1702411268608              4   

       review_confidence  review_soundness  review_presentation  \
0                     

In [5]:
# Save the new DataFrame to a different JSON file
out = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v3.json'
df_reviews.to_json(out, orient='records', indent=4)

In [ ]:
%pip install textblob
!python -m textblob.download_corpora

In [7]:
import csv
from textblob import TextBlob
from tqdm import tqdm


def compute_sentiment_polarity(review_text):
    review_text = review_text.strip()
    try:
        blob = TextBlob(review_text)
        sentiment = blob.sentiment.polarity
    except Exception:
        sentiment = ""

    return sentiment


df_reviews['sentiment_polarity'] = [
    compute_sentiment_polarity(row['total_review']) for row in tqdm(df_reviews.to_dict('records'), desc="Processing reviews")
]
df_reviews

Processing reviews: 100%|██████████| 15175/15175 [00:29<00:00, 510.35it/s]


submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  \
0      1688368213177           1702411303415              6   
1      1688505633161           1702411303319              6   
2      1688552936677           1702411303221              6   
3      1688657604892           1702411303144              6   
4      1688617232745           1702411520565              6   
...              ...                     ...            ...   
15170  1688676041356           1702411081106              6   
15171  1688449656890           1702411268900              7   
15172  1688485585833           1702411268818              5   
15173  1688665406904           1702411268706              4   
15174  1688755793651           1702411268608              4   

       review_confidence  review_soundness  review_presentation  \
0                     

In [8]:
# Save the new DataFrame to a different JSON file
out = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v4.json'
df_reviews.to_json(out, orient='records', indent=4)

# V5

In [9]:
# Read the JSON file as a pandas DataFrame
df_reviews = pd.read_json('/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v4.json')

# Display the first few rows of the DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  \
0      1688368213177           1702411303415              6   
1      1688505633161           1702411303319              6   
2      1688552936677           1702411303221              6   
3      1688657604892           1702411303144              6   
4      1688617232745           1702411520565              6   
...              ...                     ...            ...   
15170  1688676041356           1702411081106              6   
15171  1688449656890           1702411268900              7   
15172  1688485585833           1702411268818              5   
15173  1688665406904           1702411268706              4   
15174  1688755793651           1702411268608              4   

       review_confidence  review_soundness  review_presentation  \
0                     

In [10]:
import csv
import json
import torch
from transformers import AutoTokenizer, AutoModel
from tqdm import tqdm
import torch.nn.functional as F

# --- Load SPECTER model ---
model_name = "allenai/specter"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)
model.eval()

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)


def encoding_text(text):
    inputs = tokenizer(
        text,
        return_tensors="pt",
        truncation=True,
        max_length=512,
        padding=True
    ).to(device)
    
    with torch.no_grad():
        outputs = model(**inputs)
        embeddings = outputs.last_hidden_state[:, 0, :]  # [CLS] token
    
    return embeddings


def compute_relevance_score(review_text, title, abstract):
    # Encode document
    doc_emb = encoding_text(f"{title} {abstract}")

    # Encode review text
    review_emb = encoding_text(review_text)
    
    # Compute cosine similarity
    return F.cosine_similarity(doc_emb, review_emb).item()


# Compute similarity score for each row with progress bar
df_reviews['similarity_score'] = [
    compute_relevance_score(row['total_review'], row['submission_title'], row['submission_abstract'])
    for row in tqdm(df_reviews.to_dict('records'), desc="Computing similarity scores")
]

# Display the updated DataFrame
df_reviews

2025-05-08 16:43:24.962472: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1746737004.984484 1212053 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1746737004.991224 1212053 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1746737005.010641 1212053 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1746737005.010667 1212053 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1746737005.010669 1212053 computation_placer.cc:177] computation placer alr

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       review_soundness  revi

In [11]:
# Save the new DataFrame to a different JSON file
out = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v5.json'
df_reviews.to_json(out, orient='records', indent=4)

# V6

In [2]:
# Read the JSON file as a pandas DataFrame
df_reviews = pd.read_json('/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v5.json')
# Display the first few rows of the DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       review_soundness  revi

In [3]:
# Calculate the time differences and add new columns
df_reviews['paper_submission_to_review_submission_time'] = df_reviews['last_modification_date'] - df_reviews['submission_creation_date']
df_reviews['review_creation_to_review_submission_time'] = df_reviews['last_modification_date'] - df_reviews['creation_date']

# Display the updated DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       review_contribution   

In [4]:
# Convert time from milliseconds to days
df_reviews['paper_submission_to_review_submission_days'] = df_reviews['paper_submission_to_review_submission_time'] // (24 * 60 * 60 * 1000)
df_reviews['review_creation_to_review_submission_days'] = df_reviews['review_creation_to_review_submission_time'] // (24 * 60 * 60 * 1000)

# Drop the original columns to avoid redundancy
df_reviews = df_reviews.drop(columns=['paper_submission_to_review_submission_time', 'review_creation_to_review_submission_time'])

# Display the updated DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       review_contribution   

In [6]:
# Save the new DataFrame to a different JSON file
out = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v6.json'
df_reviews.to_json(out, orient='records', indent=4)

# V7

In [3]:
# Read the JSON file as a pandas DataFrame
df_reviews = pd.read_json('/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v6.json')
# Display the first few rows of the DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       review_contribution   

In [4]:
import pandas as pd
import textstat
import os
from tqdm import tqdm


# Enable tqdm for pandas apply
tqdm.pandas(desc="Scoring Readability")

# Define the readability scoring function
def readability_scores(text):
    try:
        return {
            "flesch_reading_ease": round(textstat.flesch_reading_ease(text), 4),
            "flesch_kincaid_grade": round(textstat.flesch_kincaid_grade(text), 4),
            "gunning_fog": round(textstat.gunning_fog(text), 4),
            "smog_index": round(textstat.smog_index(text), 4),
            "automated_readability_index": round(textstat.automated_readability_index(text), 4),
        }
    except:
        return {
            "flesch_reading_ease": None,
            "flesch_kincaid_grade": None,
            "gunning_fog": None,
            "smog_index": None,
            "automated_readability_index": None,
        }

readability_scores_df = df_reviews['total_review'].progress_apply(readability_scores).apply(pd.Series)
df_reviews = pd.concat([df_reviews, readability_scores_df], axis=1)
df_reviews

Scoring Readability: 100%|██████████| 15175/15175 [00:41<00:00, 367.72it/s]


submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...   mattr  \
0      1688368213177           1702411303415              6  ...  0.7494   
1      1688505633161           1702411303319              6  ...  0.7788   
2      1688552936677           1702411303221              6  ...  0.7975   
3      1688657604892           1702411303144              6  ...  0.8136   
4      1688617232745           1702411520565              6  ...  0.8162   
...              ...                     ...            ...  ...     ...   
15170  1688676041356           1702411081106              6  ...  0.7740   
15171  1688449656890           1702411268900              7  ...  0.8006   
15172  1688485585833           1702411268818              5  ...  0.7540   
15173  1688665406904           1702411268706              4  ...  0.7824   
15174  168

In [5]:
import torch
from tqdm import tqdm
from convokit import Corpus, TextParser, PolitenessStrategies, Classifier, Utterance, Speaker, download

# Check if GPU is available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Step 1: Load training corpus
print("📥 Downloading training corpus...")
train_corpus = Corpus(filename=download('wiki-politeness-annotated'))

# Step 2: Convert review data to Utterances with dummy speakers
review_utterances = []
for idx, row in tqdm(df_reviews.iterrows(), desc="🔧 Preparing Utterances", total=len(df_reviews)):
    review_text = row['total_review'].strip()
    if review_text:
        dummy_speaker = Speaker(id=f"reviewer_{idx}")
        review_utterances.append(
            Utterance(id=str(idx), text=review_text, speaker=dummy_speaker, meta={"orig_row": row})
        )

# Step 3: Build test corpus
print("📦 Building test corpus...")
test_corpus = Corpus(utterances=review_utterances)

# Step 4: Parse
print("🧠 Parsing utterances...")
parser = TextParser()
parser.transform(train_corpus)
parser.transform(test_corpus)

# Step 5: Extract politeness strategies
print("✨ Extracting politeness strategies...")
ps = PolitenessStrategies()
ps.transform(train_corpus)
ps.transform(test_corpus)

# Step 6: Train classifier
print("🎓 Training classifier...")
clf = Classifier(obj_type='utterance', pred_feats=['politeness_strategies'],
                 labeller=lambda utt: utt.meta.get("Binary") == 1)

# Move classifier to GPU
clf.device = device

# Train on GPU
clf.fit(train_corpus)

# Test on GPU
clf.transform(test_corpus)

# Step 7: Compute politeness scores and add them to the dataframe
print("📈 Computing politeness scores...")
politeness_scores = []
for utt in tqdm(test_corpus.iter_utterances(), desc="🔗 Assigning Scores"):
    try:
        score = clf.summarize(test_corpus).loc[utt.id, "pred_score"]
        politeness_scores.append(round(score, 4))
    except KeyError:
        politeness_scores.append("")

# Add politeness scores to the dataframe
df_reviews['politeness_score'] = politeness_scores

print("✅ Politeness scores added to the dataframe.")


Using device: cuda
📥 Downloading training corpus...
Dataset already exists at /home/ali/.convokit/saved-corpora/wiki-politeness-annotated


🔧 Preparing Utterances: 100%|██████████| 15175/15175 [00:01<00:00, 10152.50it/s]


📦 Building test corpus...
🧠 Parsing utterances...
✨ Extracting politeness strategies...
🎓 Training classifier...
Initialized default classification model (standard scaled logistic regression).
📈 Computing politeness scores...


🔗 Assigning Scores: 15175it [25:38,  9.86it/s]

✅ Politeness scores added to the dataframe.


In [6]:
# Save the new DataFrame to a different JSON file
out = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v7.json'
df_reviews.to_json(out, orient='records', indent=4)

In [7]:
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       sentiment_polarity  si

# V8: Final

In [28]:
# Read the JSON file as a pandas DataFrame
df_reviews = pd.read_json('/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v7.json')
# Display the first few rows of the DataFrame
df_reviews

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       sentiment_polarity  si

In [29]:
from simpletransformers.ner import NERModel, NERArgs
import pandas as pd
from tqdm import tqdm
import torch
from collections import Counter

# Define labels used by the HEDGEhog model
labels = ["C", "D", "E", "I", "N"]

# Set up model arguments
model_args = NERArgs()
model_args.labels_list = labels
model_args.silent = True
model_args.use_multiprocessing = False

# Initialize model
model = NERModel(
    model_type="bert",
    model_name="jeniakim/hedgehog",
    args=model_args,
    use_cuda=torch.cuda.is_available()
)

# Function to count each label type
def count_hedge_labels(text):
    predictions, _ = model.predict([text])
    token_labels = [list(token.values())[0] for token in predictions[0]]
    counts = Counter(token_labels)
    return {label: counts.get(label, 0) for label in labels}


# Escape brackets in the 'total_review' column; brackets [] are raising errors for hedge function. I should add \ before them.
df_reviews['total_review'] = df_reviews['total_review'].apply(
    lambda x: re.sub(r'([\[\]])', r'\\\1', x)
)

# Apply count_hedge_labels to the 'total_review' column
tqdm.pandas(desc="Counting Hedge Labels")
hedge_counts = df_reviews["total_review"].progress_apply(count_hedge_labels)

# Convert the dictionary output into separate columns
for label in labels:
    df_reviews[f"hedge_{label}"] = hedge_counts.apply(lambda x: x.get(label, 0))

df_reviews

Counting Hedge Labels:   0%|          | 0/15175 [00:00<?, ?it/s]/home/ali/Review_Quality_Benchmark/.venv/lib/python3.10/site-packages/simpletransformers/ner/ner_model.py:1643: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():
Counting Hedge Labels: 100%|██████████| 15175/15175 [06:36<00:00, 38.31it/s]


submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       flesch_kincaid_grade  

In [30]:
# Save the new DataFrame to a different JSON file
out = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v8.json'
df_reviews.to_json(out, orient='records', indent=4)

# Slice 1000

In [ ]:
import pandas as pd


input_file = '/home/ali/Review_Quality_Benchmark/data/processed/openreview_neurips2023_v8.json'

df = pd.read_json(input_file)
df

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
4        zyZkaqNnpa              15594             1683835167534   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
4      [~Aahlad_Manas_Puli1, ~Lily_H_Zhang1, ~Yoav_Wa...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
4      Don’t blame Dataset Shift! Shortcut Learning d...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
4      Common explanations for shortcut learning assu...  Reviewer_9QKU   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
4      1688617232745           1702411520565              6  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       flesch_kincaid_grade  

In [ ]:
import random

# Randomly select 1000 unique submission_number values
selected_submission_numbers = random.sample(df['submission_number'].unique().tolist(), 1000)

# Filter rows with the selected submission_number values
df_1000 = df[df['submission_number'].isin(selected_submission_numbers)]

# Display the new dataframe
df_1000

submission_id  submission_number  submission_creation_date  \
0        zyhxRc9bew              10819             1683789038840   
1        zyhxRc9bew              10819             1683789038840   
2        zyhxRc9bew              10819             1683789038840   
3        zyhxRc9bew              10819             1683789038840   
21       zsOOqjaj2z               5668             1683686700553   
...             ...                ...                       ...   
15170    00EKYYu3fD               6838             1683719044332   
15171    009LK0vLcY              10107             1683778565991   
15172    009LK0vLcY              10107             1683778565991   
15173    009LK0vLcY              10107             1683778565991   
15174    009LK0vLcY              10107             1683778565991   

                                      submission_authors  \
0      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
1      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
2      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
3      [~Hao_Sun1, ~Boris_van_Breugel2, ~Jonathan_Cra...   
21     [~Yuanyuan_Wang5, ~Xi_Geng1, ~Wei_Huang8, ~Biw...   
...                                                  ...   
15170  [~Tianyang_Hu1, ~Fei_Chen8, ~Haonan_Wang1, ~Ji...   
15171  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15172  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15173  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   
15174  [~Mehrdad_Ghadiri2, ~David_Arbour1, ~Tung_Mai1...   

                                        submission_title  \
0      What is Flagged in Uncertainty Quantification?...   
1      What is Flagged in Uncertainty Quantification?...   
2      What is Flagged in Uncertainty Quantification?...   
3      What is Flagged in Uncertainty Quantification?...   
21     Generator Identification for Linear SDEs with ...   
...                                                  ...   
15170  Complexity Matters: Rethinking the Latent Spac...   
15171  Finite Population Regression Adjustment and No...   
15172  Finite Population Regression Adjustment and No...   
15173  Finite Population Regression Adjustment and No...   
15174  Finite Population Regression Adjustment and No...   

                                     submission_abstract       reviewer  \
0      Uncertainty quantification (UQ) is essential f...  Reviewer_AvJq   
1      Uncertainty quantification (UQ) is essential f...  Reviewer_7E4k   
2      Uncertainty quantification (UQ) is essential f...  Reviewer_hHZH   
3      Uncertainty quantification (UQ) is essential f...  Reviewer_sVgx   
21     In this paper, we present conditions for ident...  Reviewer_Huoq   
...                                                  ...            ...   
15170  In generative modeling, numerous successful ap...  Reviewer_ssMC   
15171  The design and analysis of randomized experime...  Reviewer_UdXn   
15172  The design and analysis of randomized experime...  Reviewer_ZgSr   
15173  The design and analysis of randomized experime...  Reviewer_HGb9   
15174  The design and analysis of randomized experime...  Reviewer_zpw6   

       creation_date  last_modification_date  review_rating  ...  \
0      1688368213177           1702411303415              6  ...   
1      1688505633161           1702411303319              6  ...   
2      1688552936677           1702411303221              6  ...   
3      1688657604892           1702411303144              6  ...   
21     1688427159321           1702411021240              7  ...   
...              ...                     ...            ...  ...   
15170  1688676041356           1702411081106              6  ...   
15171  1688449656890           1702411268900              7  ...   
15172  1688485585833           1702411268818              5  ...   
15173  1688665406904           1702411268706              4  ...   
15174  1688755793651           1702411268608              4  ...   

       flesch_kincaid_grade  

In [ ]:
df_1000.to_json('/home/ali/Review_Quality_Benchmark/data/processed/neurips2023_1000_papers.json', orient='records')

# LLM

In [ ]:
import pandas as pd
import json
import re
import csv
import time
from tqdm import tqdm
from ollama import chat


input_file = '/home/ali/Review_Quality_Benchmark/data/processed/neurips2023_1000_papers.json'
# Load data
df = pd.read_json(input_file)

llm_fields = [
    "llm_Comprehensiveness", "llm_Vagueness", "llm_Objectivity", "llm_Fairness", "llm_Actionability", 
    "llm_Constructiveness", "llm_Relevance Alignment", "llm_Clarity and Readability", "llm_Usage of Technical Terms",
    "llm_Factuality", "llm_Overall Quality", "llm_overall_score_100", "llm_Sentiment Polarity", "llm_Politeness", 
]


# Check for missing fields and add them if not present
for field in llm_fields:
    if field not in df.columns:
        df[field] = pd.NA

# Pattern to extract JSON block
pattern = re.compile(r"<review_assessment>\s*(\{.*?\})\s*</review_assessment>", re.DOTALL)

# Define prompt template
template = """# REVIEW-QUALITY JUDGE

## 0 — ROLE

You are **ReviewInspector-LLM**, a rigorous, impartial meta-reviewer.
Your goal is to assess the quality of a single peer-review against a predefined set of criteria and to provide precise, structured evaluations.

## 1 — INPUTS

Title: {title}
Abstract: {abstract}
Review: {review_text}

## 2 — EVALUATION CRITERIA

Return **only** the scale value or label at right (no rationale text).

| #  | Criterion                    | Allowed scale / label                       | Description                                                                |
| -- | ---------------------------- | ------------------------------------------- | -------------------------------------------------------------------------- |
| 1  | **Comprehensiveness**        | integer **0-5**                             | Extent to which the review covers all key aspects of the paper.            |
| 2  | **Usage of Technical Terms** | integer **0-5**                             | Appropriateness and frequency of domain-specific vocabulary.               |
| 3  | **Factuality**               | **factual / partially factual / unfactual** | Accuracy of the statements made in the review.                             |
| 4  | **Sentiment Polarity**       | **negative / neutral / positive**           | Overall sentiment conveyed by the reviewer.                                |
| 5  | **Politeness**               | **polite / neutral / impolite**             | Tone and manner of the review language.                                    |
| 6  | **Vagueness**                | **none / low / moderate / high / extreme**  | Degree of ambiguity or lack of specificity in the review.                  |
| 7  | **Objectivity**              | integer **0-5**                             | Presence of unbiased, evidence-based commentary.                           |
| 8  | **Fairness**                 | integer **0-5**                             | Perceived impartiality and balance in judgments.                           |
| 9  | **Actionability**            | integer **0-5**                             | Helpfulness of the review in suggesting clear next steps.                  |
| 10 | **Constructiveness**         | integer **0-5**                             | Degree to which the review offers improvements rather than just criticism. |
| 11 | **Relevance Alignment**      | integer **0-5**                             | How well the review relates to the content and scope of the paper.         |
| 12 | **Clarity and Readability**  | integer **0-5**                             | Ease of understanding the review, including grammar and structure.         |
| 13 | **Overall Quality**          | integer **0-100**                           | Holistic evaluation of the review's usefulness and professionalism.        |

## 3 — SCORING GUIDELINES

For 0-5 scales:

* 5 = Outstanding
* 4 = Strong
* 3 = Adequate
* 2 = Weak
* 1 = Very weak
* 0 = Absent/irrelevant

## 4 — ANALYSIS & COMPUTATION (silent)

1. Read and understand the review in the context of the paper title and abstract.
2. Extract quantitative and qualitative signals (e.g., term usage, factual consistency, tone, clarity).
3. Map observations to the corresponding scoring scales.

## 5 — OUTPUT FORMAT (strict)  
Return **exactly one** JSON block wrapped in the tag below — **no comments or extra text**.

```json
<review_assessment>
{{
  "paper_title": "{title}",
  "criteria": {{
    "Comprehensiveness":       ...,
    "Usage of Technical Terms":   ...,
    "Factuality":    ...,
    "Sentiment Polarity":      ...,
    "Politeness":  ...,
    "Vagueness":          ...,
    "Objectivity":             ...,
    "Fairness":         ...,
    "Actionability":        ...,
    "Constructiveness":    ...,
    "Relevance Alignment":    ...,
    "Clarity and Readability":    ...,
    "Relevance Alignment":    ...,
    "Overall Quality":     ...
  }},
  "overall_score_100": ...
}}
</review_assessment>
```
"""

df

In [ ]:
# Process each row
# Set the temperature parameter for the llama model
temperature = 0
seed = 42


# Process each row
for idx, row in tqdm(df.iterrows(), total=len(df), desc="Scoring with LLM"):
    # Skip if all llm fields are already filled
    if all(pd.notna(row.get(field, pd.NA)) for field in llm_fields):
        continue
    # if idx >= 30:
    #     break

    prompt = template.format(
        title=row['submission_title'],
        abstract=row['submission_abstract'],
        review_text=row['total_review']
    )
    
    for attempt in range(5):
        try:
            response = chat("qwen3:8b", messages=[{'role': 'user', 'content': prompt}], options={'temperature': temperature, 'seed': seed})
            content = response['message']['content']
            match = pattern.search(content)
            if not match:
                raise ValueError("No JSON block found")

            parsed = json.loads(match.group(1))
            print(parsed["overall_score_100"])
            for key, val in parsed["criteria"].items():
                df.at[idx, f"llm_{key}"] = val
            df.at[idx, "llm_overall_score_100"] = parsed["overall_score_100"]

            # Save after every successful row
            # df.to_csv(input_file, index=False, quoting=csv.QUOTE_ALL)
            break

        except Exception as e:
            print(f"❌ Error at row {idx}, attempt {attempt + 1}: {e}")

In [ ]:
df.to_json('/home/ali/Review_Quality_Benchmark/data/processed/neurips2023_1000_qwen.json', orient='records')

In [ ]:
df

In [ ]:
# Filter the first 50 rows and check for rows without null values in "llm_" columns
non_null_count = df.iloc[:][[col for col in df.columns if col.startswith("llm_")]].dropna().shape[0]
print(non_null_count)
print(df.shape)